Pipeline Code
-----
Pipeline for inferring ecological interactions between microbes in treehole communities.
1. Importing tree hole data
2. Applying FlashWeave to infer co-occurrence networks
3. Applying functionInk to infer communities from co-occurrence networks
4. Visualising communities using Cytoscape

### 1 - Importing tree hole data
Importing the raw data, and converting it to the correct input format for FlashWeave.
The code below is written in the Python kernel.

In [1]:
# Importing pandas
import pandas as pd

# Importing data
asv_table = pd.read_csv('../data/seqtable_readyforanalysis.csv', sep='\t') # Importing ASV table
metadata = pd.read_csv('../data/metadata_Time0D-7D-4M_May2022_wJSDpart_ext.csv', sep='\t') # Importing metadata
taxonomy_data = pd.read_csv('../data/taxa_wsp_readyforanalysis.csv', sep='\t') # Importing taxonomy

##### Cleaning the data, and giving it the correct format. #####

# Getting rid of the samples belonging to experiment 4M:
asv_table.reset_index(inplace=True) # Making the sample ID into a column for the ASV table
asv_table.rename(columns={'index': 'sampleid'}, inplace=True) # renaming this new column to 'sampleid'
asv_table = pd.merge(asv_table, metadata, on='sampleid') # Merging metadata and asv_table by 'sampleid' so that can remove 4M samples
asv_table = asv_table[asv_table['Experiment'] != '4M'] # Taking rows which are not 4M samples

# Splitting the ASV table into starting and final communities
starting_asv_table = asv_table[asv_table['Experiment'] == '0D']
final_asv_table = asv_table[asv_table['Experiment'] != '0D']

# Splitting the metadata and ASV tables
starting_metadata = starting_asv_table[['partition']] # The metadata only contains the column for the community classes
final_metadata = final_asv_table[['partition']]
columns_to_drop = ['sampleid', 'Name.2', 'Community', 'Species', 'replicate',
       'BreakingBag', 'parent', 'Location', 'Experiment', 'Part_Time0D_17',
'Community', 'Species', 'replicate',
       'BreakingBag', 'parent', 'Location', 'Experiment', 'Part_Time0D_17',
       'Part_Time0D_6', 'Part_Time4M_64', 'Part_Time7D_rep1_2',
       'Part_Time7D_rep2_2', 'Part_Time7D_rep3_2', 'Part_Time7D_rep4_2',
       'replicate.partition', 'partition', 'ExpCompact',
       'exp.replicate.partition', 'exp.partition', 'Part_Time0D_6', 'Part_Time4M_64', 'Part_Time7D_rep1_2',
       'Part_Time7D_rep2_2', 'Part_Time7D_rep3_2', 'Part_Time7D_rep4_2',
       'replicate.partition', 'partition', 'ExpCompact',
       'exp.replicate.partition', 'exp.partition'] # Columns to drop for ASV tables
starting_asv_table = starting_asv_table.drop(columns=columns_to_drop) # The ASV tables are now in the correct input format for FlashWeave
final_asv_table = final_asv_table.drop(columns=columns_to_drop)

# Exporting to .tsv files, which can then be inputted to FlashWeave
starting_metadata.to_csv('../data/starting_metadata.tsv', sep='\t', index=False)
final_metadata.to_csv('../data/final_metadata.tsv', sep='\t', index=False)
starting_asv_table.to_csv('../data/starting_asv_table.tsv', sep='\t', index=False)
final_asv_table.to_csv('../data/final_asv_table.tsv', sep='\t', index=False)


### 2 - Applying FlashWeave
Applying heterogeneous FlashWeave to the starting communities and the final communities with classes as a factor, and applying homogeneous FlashWeave to the starting communities and the final communities - ignoring community classes. This creates 4 networks in total. The code below is written in the Julia kernel.starting_netw_results = learn_network(starting_data_pstarting_netw_results = learn_network(starting_data_path, ath, 

In [1]:
##### Applying FlashWeave #####
# Co-occurrence network for starting communities, ignoring classes
using FlashWeave
starting_data_path = "../data/starting_asv_table.tsv"
starting_netw_results = learn_network(starting_data_path, sensitive=true, heterogeneous=false)

# Co-occurrence network for final communities, ignoring classes
using FlashWeave
final_data_path = "../data/final_asv_table.tsv"
final_netw_results = learn_network(final_data_path, sensitive=true, heterogeneous=false)

# Co-occurrence network for starting communities, taking into account classes
using FlashWeave
starting_classes_data_path = "../data/starting_asv_table.tsv"
starting_classes_meta_data_path = "../data/starting_metadata.tsv"
starting_classes_netw_results = learn_network(starting_classes_data_path, starting_classes_meta_data_path, sensitive=true, heterogeneous=true)

# Co-occurrence network for final communities, taking into account classes
using FlashWeave
final_classes_data_path = "../data/final_asv_table.tsv"
final_classes_meta_data_path = "../data/final_metadata.tsv"
final_classes_netw_results = learn_network(final_classes_data_path, final_classes_meta_data_path, sensitive=true, heterogeneous=true)

# Saving the networks
save_network("../data/starting_network_output.edgelist", starting_netw_results)
save_network("../data/starting_classes_network_output.edgelist", starting_classes_netw_results)
save_network("../data/final_network_output.edgelist", final_netw_results)
save_network("../data/final_classes_network_output.edgelist", final_classes_netw_results)


### Loading data ###

### Normalizing ###

Removing variables with 0 variance (or equivalently 1 level) and samples with 0 reads
	-> discarded 0 samples and 184 variables

Normalization

### Learning interactions ###

Inferring network with FlashWeave - sensitive (conditional)

	Run information:
	sensitive - true
	heterogeneous - false
	max_k - 3
	alpha - 0.01
	sparse - false
	workers - 1
	OTUs - 1284
	MVs - 0

Automatically setting 'n_obs_min' to 20 for enhanced reliability
Computing univariate associations

Univariate degree stats:
Summary Stats:
Length:         1284
Missing Count:  0
Mean:           31.852025
Minimum:        3.000000
1st Quartile:   19.000000
Median:         25.000000
3rd Quartile:   36.000000
Maximum:        154.000000



Starting conditioning search

Preparing workers..

Done. Starting inference..
Starting convergence checks at 6857 edges.
Latest convergence step change: 0.30685
Latest convergence step change: 0.46953

Postprocessing
Complete

Finished inference.

┌ Warning: 1 factor variable with more than two categories were detected (partition), splitting it into separate dummy variables (One Hot)
└ @ FlashWeave ~/.julia/packages/FlashWeave/j91Ng/src/preprocessing.jl:63


Removing variables with 0 variance (or equivalently 1 level) and samples with 0 reads
	-> discarded 0 samples and 184 variables

Normalization

Removing meta variables with 0 variance (or equivalently 1 level)
	-> no samples or variables discarded

### Learning interactions ###

Inferring network with FlashWeaveHE - sensitive (conditional)

	Run information:
	sensitive - true
	heterogeneous - true
	max_k - 3
	alpha - 0.01
	sparse - true
	workers - 1
	OTUs - 1284
	MVs - 6

Automatically setting 'n_obs_min' to 20 for enhanced reliability
Computing univariate associations


┌ Warning: 830 variables have insufficient observations (< 20 ('n_obs_min')) and will not be used for interaction prediction
└ @ FlashWeave ~/.julia/packages/FlashWeave/j91Ng/src/learning.jl:77



Univariate degree stats:
Summary Stats:
Length:         1290
Missing Count:  0
Mean:           3.731783
Minimum:        0.000000
1st Quartile:   0.000000
Median:         0.000000
3rd Quartile:   0.000000
Maximum:        119.000000



Starting conditioning search

Preparing workers..

Done. Starting inference..
Starting convergence checks at 246 edges.
Latest convergence step change: 7.3134
Latest convergence step change: 2.05077
Latest convergence step change: 1.05591
Latest convergence step change: 0.35667
Latest convergence step change: 0.29379
Latest convergence step change: 0.1296
Latest convergence step change: 0.03436
Latest convergence step change: 0.02616

Postprocessing
Complete

Finished inference. Total time taken: 5.845s

### Loading data ###

### Normalizing ###

Removing variables with 0 variance (or equivalently 1 level) and samples with 0 reads
	-> discarded 0 samples and 261 variables

Normalization

Removing meta variables with 0 variance (or equivalently 1 level)
	-

┌ Warning: 616 variables have insufficient observations (< 20 ('n_obs_min')) and will not be used for interaction prediction
└ @ FlashWeave ~/.julia/packages/FlashWeave/j91Ng/src/learning.jl:77



Univariate degree stats:
Summary Stats:
Length:         1208
Missing Count:  0
Mean:           9.865894
Minimum:        0.000000
1st Quartile:   0.000000
Median:         0.000000
3rd Quartile:   7.000000
Maximum:        189.000000



Starting conditioning search

Preparing workers..

Done. Starting inference..
Starting convergence checks at 953 edges.
Latest convergence step change: 0.09791
Latest convergence step change: 0.36848
Latest convergence step change: 0.19409
Latest convergence step change: 0.14513
Latest convergence step change: 0.18509
Latest convergence step change: 0.28965
Latest convergence step change: 0.35655
Latest convergence step change: 0.20166
Latest convergence step change: 0.19642
Latest convergence step change: 0.25048
Latest convergence step change: 0.15153
Latest convergence step change: 0.0548
Latest convergence step change: 0.10919
Latest convergence step change: 0.19273
Latest convergence step change: 0.14766
Latest convergence step change: 0.1466
Latest 

### 2 - Applying functionInk
Converting the FlashWeave outputs into the correct input format for functionInk, and then applying functionInk to each of the 4 networks. The below code is written in the Python kernel.

In [1]:
##### Converting the FlashWeave outputs into the correct input format for functionInk #####

import pandas as pd # Importing Pandas again, as switched back to Python kernel

# Removing the headers
with open('../data/starting_network_output.edgelist', 'r') as f:
    lines = f.readlines()
with open('../data/starting_network_output.edgelist', 'w') as f:
    f.writelines(lines[2:])

with open('../data/starting_classes_network_output.edgelist', 'r') as f:
    lines = f.readlines()
with open('../data/starting_classes_network_output.edgelist', 'w') as f:
    f.writelines(lines[2:])

with open('../data/final_network_output.edgelist', 'r') as f:
    lines = f.readlines()
with open('../data/final_network_output.edgelist', 'w') as f:
    f.writelines(lines[2:])

with open('../data/final_classes_network_output.edgelist', 'r') as f:
    lines = f.readlines()
with open('../data/final_classes_network_output.edgelist', 'w') as f:
    f.writelines(lines[2:])

# Adding new headers and a column for the type of interaction (here, all assumed to be the same)
starting_network_data = pd.read_csv("../data/starting_network_output.edgelist", sep="\t", header=None, names=["ASV_A", "ASV_B", "Interaction"])
starting_network_data['Type'] = 1

starting_classes_network_data = pd.read_csv("../data/starting_classes_network_output.edgelist", sep="\t", header=None, names=["ASV_A", "ASV_B", "Interaction"])
starting_classes_network_data['Type'] = 1

final_network_data = pd.read_csv("../data/final_network_output.edgelist", sep="\t", header=None, names=["ASV_A", "ASV_B", "Interaction"])
final_network_data['Type'] = 1

final_classes_network_data = pd.read_csv("../data/final_classes_network_output.edgelist", sep="\t", header=None, names=["ASV_A", "ASV_B", "Interaction"])
final_classes_network_data['Type'] = 1

# Outputting as .tsv files
starting_network_data.to_csv('../data/starting_network_data.tsv', sep='\t', index=False, header=['#ASV_A', 'ASV_B', 'Interaction', 'Type'])
starting_classes_network_data.to_csv('../data/starting_classes_network_data.tsv', sep='\t', index=False, header=['#ASV_A', 'ASV_B', 'Interaction', 'Type'])
final_network_data.to_csv('../data/final_network_data.tsv', sep='\t', index=False, header=['#ASV_A', 'ASV_B', 'Interaction', 'Type'])
final_classes_network_data.to_csv('../data/final_classes_network_data.tsv', sep='\t', index=False, header=['#ASV_A', 'ASV_B', 'Interaction', 'Type'])

In [2]:
##### Applying functionInk #####

import os # Importing os package
os.chdir('../code/functionInk') # Moving from the directory in which this notebook is found into the root of the functionInk repository

# The first step to the pipeline - computing similarities between nodes
!./NodeSimilarity.pl -w 1 -d 0 -t 0 -f ../../data/starting_network_data.tsv
!./NodeSimilarity.pl -w 1 -d 0 -t 0 -f ../../data/starting_classes_network_data.tsv
!./NodeSimilarity.pl -w 1 -d 0 -t 0 -f ../../data/final_network_data.tsv
!./NodeSimilarity.pl -w 1 -d 0 -t 0 -f ../../data/final_classes_network_data.tsv

# The second step - clustering nodes using the similarity metrics calculated
!./NodeLinkage.pl -fn ../../data/starting_network_data.tsv -fs Nodes-Similarities_starting_network_data.tsv
!./NodeLinkage.pl -fn ../../data/starting_classes_network_data.tsv -fs Nodes-Similarities_starting_classes_network_data.tsv
!./NodeLinkage.pl -fn ../../data/final_network_data.tsv -fs Nodes-Similarities_final_network_data.tsv
!./NodeLinkage.pl -fn ../../data/final_classes_network_data.tsv -fs Nodes-Similarities_final_classes_network_data.tsv

  
**************************************************  
* Building nodes similarities NodeSimilarity.pl  *  
**************************************************  
  
>> Reading input arguments: 
~~~ The network is weighted=1 or 2/unweighted=0? Value = 1
~~~ The network is directed=1/undirected=0? Value = 0
~~~ The network has different types=1/or a single type=0? Value = 0
~~~ The network file is = ../../data/starting_network_data.tsv
 
>> Processing input arguments: 
~~~ Reading Node A from column 1
~~~ Reading Node B from column 2
~~~ Working with a weighted network -- Tanimoto coefficient
~~~ Reading weights from column 3
~~~ Working with a network with a single type of link
  
~~~ Input path:  ../../data/starting_network_data.tsv
~~~ Input file:  starting_network_data.tsv
  
 
>> Reading the network: 
~~~ The first lines for the fields read from file and after conversions are: 
..Skip header:  1
~~~ Reading fields: nodeA = ASV_1,nodeB= ASV_3, type= 1, weight = 0.2467017721710206, 
~

Extracting the partition densities. Please switch to the R kernel to run the code below.

In [1]:
##### Sourcing function that extracts partition densities #####
library(ggplot2) # Loading ggplot
source("functionInk/scripts/analysis_R/extractPartDensity.R") # Sourcing the function that extracts the partition densities
setwd("functionInk") # Moving to the functionInk repository

In [2]:
##### Extracting partition densities #####
# Importing the partition histories and cleaning them
hist_comp_starting=read.table(file="HistCompact-NL_Average_NoStop_starting_network_data.tsv")
colnames(hist_comp_starting) <- as.character(unlist(hist_comp_starting[1, ]))
hist_comp_starting <- hist_comp_starting[-1, ]
columns_to_convert <- c("Step", "Similarity", "Density", "DensityInt", "DensityExt", "NumNodesA", "NumEdgesA", 
                       "NumNodesB", "NumEdgesB", "NumNodesAB", "NumEdgesAB", "NumIntNodesA", "NumIntNodesB",
                       "NumExtNodesA", "NumExtNodesB", "NumIntNodesAB", "NumExtNodesAB", "NumIntEdgesA",
                       "NumIntEdgesB", "NumExtEdgesA", "NumExtEdgesB", "NumIntEdgesAB", "NumExtEdgesAB",
                       "NcumInt", "NcumExt", "Ncum")
hist_comp_starting[columns_to_convert] <- lapply(hist_comp_starting[columns_to_convert], as.numeric)

hist_comp_starting_classes=read.table(file="HistCompact-NL_Average_NoStop_starting_classes_network_data.tsv")
colnames(hist_comp_starting_classes) <- as.character(unlist(hist_comp_starting_classes[1, ]))
hist_comp_starting_classes <- hist_comp_starting_classes[-1, ]
hist_comp_starting_classes[columns_to_convert] <- lapply(hist_comp_starting_classes[columns_to_convert], as.numeric)

hist_comp_final=read.table(file="HistCompact-NL_Average_NoStop_final_network_data.tsv")
colnames(hist_comp_final) <- as.character(unlist(hist_comp_final[1, ]))
hist_comp_final <- hist_comp_final[-1, ]
hist_comp_final[columns_to_convert] <- lapply(hist_comp_final[columns_to_convert], as.numeric)

hist_comp_final_classes=read.table(file="HistCompact-NL_Average_NoStop_final_classes_network_data.tsv")
colnames(hist_comp_final_classes) <- as.character(unlist(hist_comp_final_classes[1, ]))
hist_comp_final_classes <- hist_comp_final_classes[-1, ]
hist_comp_final_classes[columns_to_convert] <- lapply(hist_comp_final_classes[columns_to_convert], as.numeric)


# Calculating partition densities, plotting them, and moving the plot into results
print("Starting network partition densities:")
part_density_starting=extractPartDensity(hist.comp=hist_comp_starting, plot = TRUE)
system(paste("mv", "figures/Plot_PartitionDensityVsStep.pdf", "../../results/starting_Plot_PartitionDensityVsStep.pdf"))
print("Step of the clustering in which the maximum of the total partition density was found: ")
part_density_starting$total_dens_step
print("Step of the clustering in which the maximum of the internal partition density was found ")
part_density_starting$int_dens_step
print("Step of the clustering in which the maximum of the external partition density was found: ")
part_density_starting$ext_dens_step

print("Starting classes network partition densities:")
part_density_starting_classes=extractPartDensity(hist.comp=hist_comp_starting_classes, plot = TRUE)
system(paste("mv", "figures/Plot_PartitionDensityVsStep.pdf", "../../results/starting_classes_Plot_PartitionDensityVsStep.pdf"))
print("Step of the clustering in which the maximum of the total partition density was found: ")
part_density_starting_classes$total_dens_step
print("Step of the clustering in which the maximum of the internal partition density was found ")
part_density_starting_classes$int_dens_step
print("Step of the clustering in which the maximum of the external partition density was found: ")
part_density_starting_classes$ext_dens_step

print("Final network partition densities:")
part_density_final=extractPartDensity(hist.comp=hist_comp_final, plot = TRUE)
system(paste("mv", "figures/Plot_PartitionDensityVsStep.pdf", "../../results/final_Plot_PartitionDensityVsStep.pdf"))
print("Step of the clustering in which the maximum of the total partition density was found: ")
part_density_final$total_dens_step
print("Step of the clustering in which the maximum of the internal partition density was found ")
part_density_final$int_dens_step
print("Step of the clustering in which the maximum of the external partition density was found: ")
part_density_final$ext_dens_step

print("Final classes network partition densities:")
part_density_final_classes=extractPartDensity(hist.comp=hist_comp_final_classes, plot = TRUE)
system(paste("mv", "figures/Plot_PartitionDensityVsStep.pdf", "../../results/final_classes_Plot_PartitionDensityVsStep.pdf"))
print("Step of the clustering in which the maximum of the total partition density was found: ")
part_density_final_classes$total_dens_step
print("Step of the clustering in which the maximum of the internal partition density was found ")
part_density_final_classes$int_dens_step
print("Step of the clustering in which the maximum of the external partition density was found: ")
part_density_final_classes$ext_dens_step


[1] "Starting network partition densities:"
[1] "-- The maximum value of the total partition density is 0.1149 found at step = 857"
[1] "-- The maximum value of the internal partition density is 0.0813 found at step = 1004"
[1] "-- The maximum value of the external partition density is 0.0475 found at step = 663"
[1] "Step of the clustering in which the maximum of the total partition density was found: "


[1] 857

[1] "Step of the clustering in which the maximum of the internal partition density was found "


[1] 1004

[1] "Step of the clustering in which the maximum of the external partition density was found: "


...

[1] 328

[1] "Step of the clustering in which the maximum of the internal partition density was found "


[1] 398

[1] "Step of the clustering in which the maximum of the external partition density was found: "


[1] 262

Obtaining communities. Please switch to the Python kernel to run the code below.

In [1]:
import os # Importing os again, as switched back to Python kernel
os.chdir('functionInk') # Moving from the directory in which this notebook is found into the root of the functionInk repository

In [2]:
##### Running the clustering until the step at which the total partition density is reached #####
!./NodeLinkage.pl -fn ../../data/starting_network_data.tsv -fs Nodes-Similarities_starting_network_data.tsv -s step -v 857
!./NodeLinkage.pl -fn ../../data/starting_classes_network_data.tsv -fs Nodes-Similarities_starting_classes_network_data.tsv -s step -v 214
!./NodeLinkage.pl -fn ../../data/final_network_data.tsv -fs Nodes-Similarities_final_network_data.tsv -s step -v 861
!./NodeLinkage.pl -fn ../../data/final_classes_network_data.tsv -fs Nodes-Similarities_final_classes_network_data.tsv -s step -v 328

##### Moving the output files from the functionInk pipeline #####
# Moving the node similarity files to the results folder
source_file = 'Nodes-Similarities_starting_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'Nodes-Similarities_starting_classes_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'Nodes-Similarities_final_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'Nodes-Similarities_final_classes_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

# Moving the compact node clustering history files
source_file = 'HistCompact-NL_Average_NoStop_starting_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'HistCompact-NL_Average_NoStop_starting_classes_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'HistCompact-NL_Average_NoStop_final_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'HistCompact-NL_Average_NoStop_final_classes_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

# Moving the detailed node clustering history files with the stop
source_file = 'HistExtend-NL_Average_NoStop_starting_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'HistExtend-NL_Average_NoStop_starting_classes_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'HistExtend-NL_Average_NoStop_final_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'HistExtend-NL_Average_NoStop_final_classes_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

# Moving the compact node clustering history files with the stop
source_file = 'HistCompact-NL_Average_StopStep-857_starting_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'HistCompact-NL_Average_StopStep-214_starting_classes_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'HistCompact-NL_Average_StopStep-861_final_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'HistCompact-NL_Average_StopStep-328_final_classes_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

# Moving the extended node clustering history files with the stop
source_file = 'HistExtend-NL_Average_StopStep-857_starting_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'HistExtend-NL_Average_StopStep-214_starting_classes_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'HistExtend-NL_Average_StopStep-861_final_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'HistExtend-NL_Average_StopStep-328_final_classes_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

# Moving the cluster description files
source_file = 'Clusters-NL_Average_StopStep-857_starting_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'Clusters-NL_Average_StopStep-214_starting_classes_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'Clusters-NL_Average_StopStep-861_final_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'Clusters-NL_Average_StopStep-328_final_classes_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

# Moving the file describing the cluster to which each node belongs
source_file = 'Partition-NL_Average_StopStep-857_starting_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'Partition-NL_Average_StopStep-214_starting_classes_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'Partition-NL_Average_StopStep-861_final_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

source_file = 'Partition-NL_Average_StopStep-328_final_classes_network_data.tsv'
destination_directory = '../../results'
file_name = os.path.basename(source_file)
destination_path = os.path.join(destination_directory, file_name)
os.rename(source_file, destination_path)

>> Reading input arguments: 
~~~ The network file is = ../../data/starting_network_data.tsv
~~~ The similarity file is = Nodes-Similarities_starting_network_data.tsv
~~~ The clustering will run until step
~~~ value as stopping criteria = 857
~~~ Reading the similarity from column  = 3
~~~ Clustering with = Average
  
***********************************************  
* Finding communities with nodes clustering   *  
***********************************************  
  
~~ FIELDS for the FIRST FILE
~~~ Reading Node A from column 1
~~~ Reading Node B from column 2
~~~ Reading Similarities from column 3
~~ FIELDS for the SECOND FILE
~~~ Reading Node A from column 1
~~~ Reading Node B from column 2
~~~ Reading Similarities from column 3
~~ CLUSTERING parameters: 
~~~ Performing a clustering with Average Linkage method
~~~ Clustering and recovering classification at step: 857
  
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
  
~~ Opening the first input file: 
~~~ Input path:  Nodes-Similarities_startin

4 - Visualisation in Cytoscape
-----

Cytoscape visualisations of the four networks can be found in the results folder.